In [ ]:
!pip install category_encoders
!pip install optuna
!pip install xgboost
!pip install catboost
import datetime
import pandas as pd
import numpy as np
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import SimpleImputer, IterativeImputer
from sklearn.model_selection import cross_validate, train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder, LabelEncoder
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.decomposition import PCA
from sklearn.ensemble import RandomForestClassifier
from xgboost import XGBClassifier
import category_encoders as ce
import optuna
from sklearn.model_selection import cross_val_predict, StratifiedKFold, cross_val_score
from sklearn.metrics import f1_score
from sklearn.base import clone
from catboost import CatBoostClassifier


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.9/81.9 kB 907.4 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.8/10.8 MB 46.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.9/233.9 kB 21.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 380.1/380.1 kB 2.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.4/233.4 kB 11.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 26.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 616.0/616.0 kB 34.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 297.1/297.1 MB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.2/98.2 MB 8.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.1/47.1 kB 5.0 MB/s eta 0:00:00


In [ ]:
df = pd.read_csv("https://drive.google.com/uc?export=download&id=1eYCKuqJda4bpzXBVnqXylg0qQwvpUuum")

df['new_opinion'] = df['opinion_h1n1_vacc_effective'] - df['opinion_h1n1_risk']

X = df.drop('h1n1_vaccine', axis=1)
y = df['h1n1_vaccine']


In [ ]:
    numeric_features = [
        "h1n1_concern",
        "h1n1_knowledge",
        "behavioral_antiviral_meds",
        "behavioral_avoidance",
        "behavioral_face_mask",
        "behavioral_wash_hands",
        "behavioral_large_gatherings",
        "behavioral_outside_home",
        "behavioral_touch_face",
        "doctor_recc_h1n1",
        "doctor_recc_seasonal",
        "chronic_med_condition",
        "child_under_6_months",
        "health_worker",
        "health_insurance",
        "opinion_h1n1_vacc_effective",
        "opinion_h1n1_risk",
        "opinion_h1n1_sick_from_vacc",
        "opinion_seas_vacc_effective",
        "opinion_seas_risk",
        "opinion_seas_sick_from_vacc",
        "household_adults",
        "household_children",
        "new_opinion"
    ]

    categorical_features = [
        "age_group",
        "education",
        "race",
        "sex",
        "income_poverty",
        "marital_status",
        "rent_or_own",
        "employment_status",
        "hhs_geo_region",
        "census_msa",
        "employment_industry",
        "employment_occupation"
    ]

In [ ]:
# Impute missing values for numerical features
imp = SimpleImputer(strategy="mean")
#imp = IterativeImputer()
X[numeric_features] = imp.fit_transform(X[numeric_features])

# Apply James-Stein encoding to categorical features
encoder = ce.JamesSteinEncoder(cols=categorical_features)
X = encoder.fit_transform(X, y)

# Ensure feature names are valid for XGBoost
X.columns = [col.replace('[', '_').replace(']', '_').replace('<', '_').replace('>', '_').replace(' ', '_') for col in X.columns]

In [ ]:
#[I 2024-05-27 16:41:59,188] Trial 830 finished with value: 0.7644653481195467 and parameters: {'n_estimators': 597, 'max_depth': 8, 'min_child_weight': 9, 'learning_rate': 0.08409389583530244, 'gamma': 1.9467084526621292, 'subsample': 0.7046357446258533, 'colsample_bytree': 0.971631194938861, 'lambda': 9.830081648905782, 'alpha': 0.9012375383399465}. Best is trial 830 with value: 0.7644653481195467.
#[I 2024-05-27 18:18:27,880] Trial 56 finished with value: 0.7650417553191581 and parameters: {'n_estimators': 773, 'max_depth': 15, 'min_samples_split': 15, 'min_samples_leaf': 5, 'max_features': 0.5216065091561903}. Best is trial 56 with value: 0.7650417553191581.
# Define previous best parameters
best_params_xgb = {'n_estimators': 597, 'max_depth': 8, 'min_child_weight': 9, 'learning_rate': 0.08409389583530244, 'gamma': 1.9467084526621292, 'subsample': 0.7046357446258533, 'colsample_bytree': 0.971631194938861, 'lambda': 9.830081648905782, 'alpha': 0.9012375383399465} #0.7644653481195467
best_params_rf = {'n_estimators': 773, 'max_depth': 15, 'min_samples_split': 15, 'min_samples_leaf': 5, 'max_features': 0.5216065091561903} #0.7650417553191581
best_params_cat = {'depth': 5, 'learning_rate': 0.02792210185383513, 'iterations': 617, 'l2_leaf_reg': 8.728594027544975, 'border_count': 98, 'scale_pos_weight': 1.4026035793558485}


def optimize_base_model(trial, model, X, y):
    if model == 'xgb':
        params = {
          'objective': 'binary:logistic',
          'n_estimators': trial.suggest_int('n_estimators', 50, 1000),
          'max_depth': trial.suggest_int('max_depth', 3, 15),
          'min_child_weight': trial.suggest_int('min_child_weight', 1, 10),
          'learning_rate': trial.suggest_float('learning_rate', 0, 0.3),
          'gamma': trial.suggest_float('gamma', 0, 10),
          'subsample': trial.suggest_float('subsample', 0.5, 1),
          'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1),
          'lambda': trial.suggest_float('lambda', 0, 10),
          'alpha': trial.suggest_float('alpha', 0, 10),
          'use_label_encoder': False,
          'eval_metric': 'logloss',
          'booster': 'gbtree'
        }
        model = XGBClassifier(random_state=0, **params)
    elif model == 'cat':
        params = {
            'objective': 'Logloss',
            'depth': trial.suggest_int('depth', 3, 15),
            'learning_rate': trial.suggest_float('learning_rate', 0.001, 0.3),
            'iterations': trial.suggest_int('iterations', 50, 1000),
            'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-3, 10.0),
            'border_count': trial.suggest_int('border_count', 1, 255),
            'scale_pos_weight': trial.suggest_float('scale_pos_weight', 0.5, 5.0),
            'eval_metric': 'Logloss',
            'loss_function': 'Logloss'
        }
        model = CatBoostClassifier(**params, verbose=0)
    elif model == 'rf':
        params = {
            'criterion': "log_loss",
            'n_estimators': trial.suggest_int('n_estimators', 50, 1000),
            'max_depth': trial.suggest_int('max_depth', 3, 15),
            'min_samples_split': trial.suggest_int('min_samples_split', 2, 20),
            'min_samples_leaf': trial.suggest_int('min_samples_leaf', 1, 20),
            'max_features': trial.suggest_float('max_features', 0.1, 1.0),
            'class_weight': 'balanced'
        }
        model = RandomForestClassifier(**params)

    skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=0)
    return cross_val_score(model, X, y, cv=skf, scoring='f1_macro').mean()

def objective_xgb(trial):
    return optimize_base_model(trial, 'xgb', X, y)

def objective_rf(trial):
    return optimize_base_model(trial, 'rf', X, y)

def objective_cat(trial):
    return optimize_base_model(trial, 'cat', X, y)

#study_xgb = optuna.create_study(direction='maximize', study_name = 'xgb')
#study_xgb.enqueue_trial(best_params_xgb)
#study_xgb.optimize(objective_xgb, n_trials=1000)
#best_params_xgb = study_xgb.best_params

#study_rf = optuna.create_study(direction='maximize', study_name = 'rf')
#study_rf.enqueue_trial(best_params_rf)
#study_rf.optimize(objective_rf, n_trials=1000)
#best_params_rf = study_rf.best_params

study_cat = optuna.create_study(direction='maximize', study_name = 'cat')
#study_cat.enqueue_trial(best_params_cat)
study_cat.optimize(objective_cat, n_trials=100)
best_params_cat = study_cat.best_params


[I 2024-05-27 19:33:02,500] A new study created in memory with name: cat
[I 2024-05-27 19:34:26,138] Trial 0 finished with value: 0.7531561225139465 and parameters: {'depth': 10, 'learning_rate': 0.19920851120879715, 'iterations': 756, 'l2_leaf_reg': 9.152501753116555, 'border_count': 114, 'scale_pos_weight': 3.862147111305408}. Best is trial 0 with value: 0.7531561225139465.
[I 2024-05-27 19:34:32,969] Trial 1 finished with value: 0.7314490636617137 and parameters: {'depth': 3, 'learning_rate': 0.25646837506024267, 'iterations': 342, 'l2_leaf_reg': 1.6895081595708112, 'border_count': 197, 'scale_pos_weight': 4.566631574280528}. Best is trial 0 with value: 0.7531561225139465.
[I 2024-05-27 19:38:58,273] Trial 2 finished with value: 0.7382321034632126 and parameters: {'depth': 14, 'learning_rate': 0.08288481983219965, 'iterations': 269, 'l2_leaf_reg': 2.914922605498524, 'border_count': 212, 'scale_pos_weight': 0.7268078314714593}. Best is trial 0 with value: 0.7531561225139465.
[I 2024-

In [ ]:
print(best_params_xgb)
print(best_params_rf)
print(best_params_cat)

{'n_estimators': 597, 'max_depth': 8, 'min_child_weight': 9, 'learning_rate': 0.08409389583530244, 'gamma': 1.9467084526621292, 'subsample': 0.7046357446258533, 'colsample_bytree': 0.971631194938861, 'lambda': 9.830081648905782, 'alpha': 0.9012375383399465}
{'n_estimators': 773, 'max_depth': 15, 'min_samples_split': 15, 'min_samples_leaf': 5, 'max_features': 0.5216065091561903}
{'depth': 5, 'learning_rate': 0.02792210185383513, 'iterations': 617, 'l2_leaf_reg': 8.728594027544975, 'border_count': 98, 'scale_pos_weight': 1.4026035793558485}


In [ ]:
# Train base models with best parameters
xgb_model = XGBClassifier(random_state=0, **best_params_xgb)
rf_model = RandomForestClassifier(random_state=0, **best_params_rf)
cat_model = CatBoostClassifier(random_state=0, **best_params_cat)

skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=0)
meta_features = np.zeros((X.shape[0], 3))

meta_features[:, 0] = cross_val_predict(xgb_model, X, y, cv=skf, method='predict_proba')[:, 1]
meta_features[:, 1] = cross_val_predict(cat_model, X, y, cv=skf, method='predict_proba')[:, 1]
meta_features[:, 2] = cross_val_predict(rf_model, X, y, cv=skf, method='predict_proba')[:, 1]


0:	learn: 0.6764461	total: 6.82ms	remaining: 4.2s
1:	learn: 0.6597143	total: 13.7ms	remaining: 4.2s
2:	learn: 0.6439903	total: 19.1ms	remaining: 3.9s
3:	learn: 0.6305148	total: 24.7ms	remaining: 3.79s
4:	learn: 0.6167916	total: 30.1ms	remaining: 3.68s
5:	learn: 0.6044907	total: 35.3ms	remaining: 3.6s
6:	learn: 0.5923862	total: 40.5ms	remaining: 3.53s
7:	learn: 0.5806781	total: 45.7ms	remaining: 3.48s
8:	learn: 0.5705128	total: 51.1ms	remaining: 3.45s
9:	learn: 0.5611158	total: 56.2ms	remaining: 3.41s
10:	learn: 0.5526997	total: 61.1ms	remaining: 3.37s
11:	learn: 0.5442355	total: 66.8ms	remaining: 3.37s
12:	learn: 0.5362593	total: 72ms	remaining: 3.34s
13:	learn: 0.5284200	total: 77.2ms	remaining: 3.33s
14:	learn: 0.5211490	total: 84.2ms	remaining: 3.38s
15:	learn: 0.5154098	total: 89.7ms	remaining: 3.37s
16:	learn: 0.5093031	total: 95.2ms	remaining: 3.36s
17:	learn: 0.5040654	total: 102ms	remaining: 3.38s
18:	learn: 0.4992491	total: 107ms	remaining: 3.35s
19:	learn: 0.4938423	total: 11

In [ ]:
#Trial 42 finished with value: 0.7729472739605427 and parameters: {'depth': 5, 'learning_rate': 0.04162699126230205, 'iterations': 173, 'l2_leaf_reg': 5.660610566431028, 'border_count': 14, 'scale_pos_weight': 1.6445593720521026}. Best is trial 42 with value: 0.7729472739605427.

# Define the optimization function for the CatBoost meta-learner
def optimize_meta_learner(trial):
    params = {
            'objective': 'Logloss',
            'depth': trial.suggest_int('depth', 3, 15),
            'learning_rate': trial.suggest_float('learning_rate', 0.001, 0.3),
            'iterations': trial.suggest_int('iterations', 50, 1000),
            'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-3, 10.0),
            'border_count': trial.suggest_int('border_count', 1, 255),
            'scale_pos_weight': trial.suggest_float('scale_pos_weight', 0.5, 5.0),
            'eval_metric': 'Logloss',
            'loss_function': 'Logloss'
        }
    meta_learner = CatBoostClassifier(**params)
    return cross_val_score(meta_learner, meta_features, y, cv=skf, scoring='f1_macro').mean()

# Optimize hyperparameters for the CatBoost meta-learner
study_meta = optuna.create_study(direction='maximize')
study_meta.optimize(optimize_meta_learner, n_trials=50)
best_params_meta = study_meta.best_params

#best_params_meta =


# Train the meta-learner with the best parameters
meta_learner = CatBoostClassifier(random_state=0, **best_params_meta)
meta_learner.fit(meta_features, y)

# Evaluate the meta-learner
meta_features_test = np.column_stack([
    cross_val_predict(xgb_model, X, y, cv=skf, method='predict_proba')[:, 1],
    cross_val_predict(cat_model, X, y, cv=skf, method='predict_proba')[:, 1],
    cross_val_predict(rf_model, X, y, cv=skf, method='predict_proba')[:, 1]
])

meta_predictions = meta_learner.predict(meta_features_test)
meta_f1_score = f1_score(y, meta_predictions, average='macro')
print(f"Meta-Learner F1 Macro Score: {meta_f1_score}")

[I 2024-05-27 23:11:03,308] A new study created in memory with name: no-name-c315d3c6-9abc-4e37-9821-e94a41e1fc8d


0:	learn: 0.5653186	total: 361ms	remaining: 5m 3s
1:	learn: 0.5043843	total: 755ms	remaining: 5m 17s
2:	learn: 0.4768857	total: 764ms	remaining: 3m 33s
3:	learn: 0.4645577	total: 775ms	remaining: 2m 42s
4:	learn: 0.4544410	total: 1.15s	remaining: 3m 12s
5:	learn: 0.4510455	total: 1.16s	remaining: 2m 41s
6:	learn: 0.4487631	total: 1.16s	remaining: 2m 18s
7:	learn: 0.4455120	total: 1.36s	remaining: 2m 21s
8:	learn: 0.4416776	total: 1.73s	remaining: 2m 39s
9:	learn: 0.4407795	total: 1.74s	remaining: 2m 24s
10:	learn: 0.4391363	total: 2.13s	remaining: 2m 40s
11:	learn: 0.4390774	total: 2.13s	remaining: 2m 27s
12:	learn: 0.4361883	total: 2.5s	remaining: 2m 39s
13:	learn: 0.4361126	total: 2.51s	remaining: 2m 28s
14:	learn: 0.4349894	total: 2.56s	remaining: 2m 21s
15:	learn: 0.4333927	total: 2.92s	remaining: 2m 30s
16:	learn: 0.4316870	total: 3.28s	remaining: 2m 39s
17:	learn: 0.4315955	total: 3.28s	remaining: 2m 30s
18:	learn: 0.4303519	total: 3.67s	remaining: 2m 38s
19:	learn: 0.4301129	tot

[I 2024-05-27 23:26:13,165] Trial 0 finished with value: 0.7295821605775075 and parameters: {'depth': 15, 'learning_rate': 0.26765999191532736, 'iterations': 842, 'l2_leaf_reg': 1.2508038133010744, 'border_count': 16, 'scale_pos_weight': 3.6698816883347822}. Best is trial 0 with value: 0.7295821605775075.


0:	learn: 0.5672832	total: 13.1ms	remaining: 8.83s
1:	learn: 0.4798525	total: 19.7ms	remaining: 6.62s
2:	learn: 0.4187071	total: 26ms	remaining: 5.81s
3:	learn: 0.3786851	total: 32ms	remaining: 5.35s
4:	learn: 0.3523242	total: 37.6ms	remaining: 5.03s
5:	learn: 0.3322367	total: 43.9ms	remaining: 4.88s
6:	learn: 0.3185168	total: 49.2ms	remaining: 4.68s
7:	learn: 0.3082818	total: 55.3ms	remaining: 4.6s
8:	learn: 0.3018368	total: 61ms	remaining: 4.5s
9:	learn: 0.2965581	total: 65.9ms	remaining: 4.37s
10:	learn: 0.2929955	total: 71ms	remaining: 4.28s
11:	learn: 0.2905161	total: 76.6ms	remaining: 4.22s
12:	learn: 0.2884002	total: 82ms	remaining: 4.16s
13:	learn: 0.2869492	total: 87.8ms	remaining: 4.13s
14:	learn: 0.2855178	total: 93.6ms	remaining: 4.11s
15:	learn: 0.2844291	total: 99.3ms	remaining: 4.08s
16:	learn: 0.2836728	total: 106ms	remaining: 4.08s
17:	learn: 0.2830245	total: 111ms	remaining: 4.03s
18:	learn: 0.2826367	total: 116ms	remaining: 4.01s
19:	learn: 0.2822247	total: 122ms	rem

[I 2024-05-27 23:26:33,386] Trial 1 finished with value: 0.7351552302196298 and parameters: {'depth': 6, 'learning_rate': 0.1266496768623394, 'iterations': 673, 'l2_leaf_reg': 1.2667765778640994, 'border_count': 37, 'scale_pos_weight': 0.6405671649933187}. Best is trial 1 with value: 0.7351552302196298.


...

0:	learn: 0.6565779	total: 6.19ms	remaining: 1.25s
1:	learn: 0.6250790	total: 12.2ms	remaining: 1.23s
2:	learn: 0.5965025	total: 17.9ms	remaining: 1.19s
3:	learn: 0.5728757	total: 22.3ms	remaining: 1.11s
4:	learn: 0.5522922	total: 27ms	remaining: 1.07s
5:	learn: 0.5353256	total: 31.9ms	remaining: 1.05s
6:	learn: 0.5198125	total: 36.6ms	remaining: 1.02s
7:	learn: 0.5059993	total: 40.6ms	remaining: 991ms
8:	learn: 0.4944562	total: 45.4ms	remaining: 979ms
9:	learn: 0.4840053	total: 49.6ms	remaining: 957ms
10:	learn: 0.4753203	total: 53.5ms	remaining: 934ms
11:	learn: 0.4679232	total: 57.8ms	remaining: 920ms
12:	learn: 0.4604543	total: 62.3ms	remaining: 910ms
13:	learn: 0.4548541	total: 66.1ms	remaining: 892ms
14:	learn: 0.4497813	total: 72ms	remaining: 902ms
15:	learn: 0.4455959	total: 76.5ms	remaining: 895ms
16:	learn: 0.4410997	total: 80.6ms	remaining: 882ms
17:	learn: 0.4374870	total: 85.2ms	remaining: 876ms
18:	learn: 0.4344708	total: 89.8ms	remaining: 870ms
19:	learn: 0.4316713	total

[I 2024-05-28 00:08:33,284] Trial 48 finished with value: 0.7715827802865297 and parameters: {'depth': 4, 'learning_rate': 0.060257819362032346, 'iterations': 203, 'l2_leaf_reg': 7.0129563492765925, 'border_count': 64, 'scale_pos_weight': 1.7856235964577745}. Best is trial 42 with value: 0.7729472739605427.


186:	learn: 0.3998564	total: 808ms	remaining: 69.1ms
187:	learn: 0.3997748	total: 812ms	remaining: 64.8ms
188:	learn: 0.3996921	total: 817ms	remaining: 60.5ms
189:	learn: 0.3996191	total: 821ms	remaining: 56.2ms
190:	learn: 0.3995904	total: 826ms	remaining: 51.9ms
191:	learn: 0.3994815	total: 831ms	remaining: 47.6ms
192:	learn: 0.3994433	total: 835ms	remaining: 43.3ms
193:	learn: 0.3993799	total: 840ms	remaining: 39ms
194:	learn: 0.3993364	total: 844ms	remaining: 34.6ms
195:	learn: 0.3992736	total: 849ms	remaining: 30.3ms
196:	learn: 0.3992177	total: 853ms	remaining: 26ms
197:	learn: 0.3991622	total: 857ms	remaining: 21.6ms
198:	learn: 0.3991173	total: 861ms	remaining: 17.3ms
199:	learn: 0.3990756	total: 865ms	remaining: 13ms
200:	learn: 0.3989973	total: 870ms	remaining: 8.65ms
201:	learn: 0.3989546	total: 875ms	remaining: 4.33ms
202:	learn: 0.3988788	total: 879ms	remaining: 0us
0:	learn: 0.6007456	total: 2.41ms	remaining: 207ms
1:	learn: 0.5342179	total: 5.17ms	remaining: 220ms
2:	lea

[I 2024-05-28 00:08:34,896] Trial 49 finished with value: 0.7592414589044304 and parameters: {'depth': 6, 'learning_rate': 0.18057264106668097, 'iterations': 87, 'l2_leaf_reg': 1.0093250386105241, 'border_count': 24, 'scale_pos_weight': 0.9630632197440998}. Best is trial 42 with value: 0.7729472739605427.


73:	learn: 0.3272228	total: 192ms	remaining: 33.8ms
74:	learn: 0.3271576	total: 195ms	remaining: 31.2ms
75:	learn: 0.3270675	total: 198ms	remaining: 28.6ms
76:	learn: 0.3270037	total: 200ms	remaining: 26ms
77:	learn: 0.3269367	total: 203ms	remaining: 23.4ms
78:	learn: 0.3268319	total: 205ms	remaining: 20.8ms
79:	learn: 0.3266780	total: 208ms	remaining: 18.2ms
80:	learn: 0.3266118	total: 211ms	remaining: 15.6ms
81:	learn: 0.3264900	total: 213ms	remaining: 13ms
82:	learn: 0.3263831	total: 216ms	remaining: 10.4ms
83:	learn: 0.3263479	total: 218ms	remaining: 7.79ms
84:	learn: 0.3263192	total: 220ms	remaining: 5.19ms
85:	learn: 0.3260696	total: 223ms	remaining: 2.6ms
86:	learn: 0.3260121	total: 226ms	remaining: 0us
0:	learn: 0.6738458	total: 2.88ms	remaining: 496ms
1:	learn: 0.6559476	total: 5.53ms	remaining: 473ms
2:	learn: 0.6392368	total: 8.47ms	remaining: 480ms
3:	learn: 0.6238263	total: 10.8ms	remaining: 456ms
4:	learn: 0.6095917	total: 13.3ms	remaining: 448ms
5:	learn: 0.5964320	total

In [ ]:
xgb_model.fit(X, y)
rf_model.fit(X, y)
cat_model.fit(X, y)
# Load competition data
X_comp = pd.read_csv("https://drive.google.com/uc?export=download&id=1SmFBoNh7segI1Ky92mfeIe6TpscclMwQ")

# Create new feature in competition data
X_comp['new_opinion'] = X_comp['opinion_h1n1_vacc_effective'] - X_comp['opinion_h1n1_risk']

# Apply the same preprocessing to the competition data
X_comp[numeric_features] = imp.transform(X_comp[numeric_features])
X_comp = encoder.transform(X_comp)

# Generate meta-features for competition data
meta_features_comp = np.zeros((X_comp.shape[0], 3))
meta_features_comp[:, 0] = xgb_model.predict_proba(X_comp)[:, 1]
meta_features_comp[:, 1] = cat_model.predict_proba(X_comp)[:, 1]
meta_features_comp[:, 2] = rf_model.predict_proba(X_comp)[:, 1]

# Make final predictions with the meta-learner
final_predictions_comp = meta_learner.predict(meta_features_comp)

# Prepare the submission file
my_submission = pd.DataFrame({'predicted': final_predictions_comp})
print(len(my_submission))
print(my_submission.head(10))

# Save the predictions to a CSV file
my_submission.to_csv('my_submission_essemble.csv', index=False)

0:	learn: 0.6763215	total: 6.93ms	remaining: 4.27s
1:	learn: 0.6595585	total: 13.3ms	remaining: 4.08s
2:	learn: 0.6447407	total: 19.1ms	remaining: 3.92s
3:	learn: 0.6292344	total: 25.1ms	remaining: 3.85s
4:	learn: 0.6154390	total: 30.2ms	remaining: 3.7s
5:	learn: 0.6024542	total: 35.6ms	remaining: 3.63s
6:	learn: 0.5897847	total: 41.1ms	remaining: 3.58s
7:	learn: 0.5783440	total: 46.8ms	remaining: 3.56s
8:	learn: 0.5684479	total: 52.7ms	remaining: 3.56s
9:	learn: 0.5588305	total: 58.4ms	remaining: 3.54s
10:	learn: 0.5503458	total: 64.6ms	remaining: 3.56s
11:	learn: 0.5423343	total: 70ms	remaining: 3.53s
12:	learn: 0.5345346	total: 75.9ms	remaining: 3.53s
13:	learn: 0.5272441	total: 81.7ms	remaining: 3.52s
14:	learn: 0.5205475	total: 87.4ms	remaining: 3.51s
15:	learn: 0.5145185	total: 93.5ms	remaining: 3.51s
16:	learn: 0.5083379	total: 99.7ms	remaining: 3.52s
17:	learn: 0.5020466	total: 106ms	remaining: 3.52s
18:	learn: 0.4969882	total: 112ms	remaining: 3.52s
19:	learn: 0.4922077	total: